In [9]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException
import time
import os
import json
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.common.keys import Keys

# 다운로드 경로
# download_dir = "C:\\KIMUJUNG\\team_project\\final_project\\crawling\\download_json"
download_dir = ".\\download_json"
driver = webdriver.Chrome()
# output_path = os.path.join(download_dir, "products_babys.json")

driver.get('https://gift.kakao.com/home?targetType=ALL&rankType=MANY_WISH_RECEIVE&priceRange=20000_29999')
time.sleep(1)

        
# 유아동/반려
for i in range(10, 11): # 11개
    products_data = []

    # 카테고리 클릭
    xpath_1 = f'//*[@id="kakaoWrap"]/sc-gift-header/header/lib-container-pc/div[1]/div/div[1]/button'
    btn_1 = driver.find_element(By.XPATH, xpath_1)
    btn_1.click()
    time.sleep(1)

    # 유아동/반려
    xpath_2 = f'/html/body/cu-popup-container2/cu-popup-wrapper2/ng-component/app-pc-category-tab/div/div/div[2]/div/div[1]/app-pc-category-l-category/ul/li[10]/a'
    btn_2 = driver.find_element(By.XPATH, xpath_2)
    btn_2.click()
    time.sleep(2)
    name_txt1 = driver.find_element(By.XPATH, xpath_2).text
    print(name_txt1)

    try:        
        # 세부 카테고리
        xpath_3 = f'//*[@id="tabpan-9"]/ul/li[{i}]/gc-link'
        name_txt2 = driver.find_element(By.XPATH, xpath_3).text
        print(name_txt2)
        output_path = os.path.join(download_dir, "products_baby_"+ name_txt2.replace("/", "") +".json")
        
        btn_3 = driver.find_element(By.XPATH, xpath_3+"/a")
        btn_3.click()
        time.sleep(2)
        
        original_window = driver.current_window_handle

        # 상품 선택
        for j in range(1, 101):
            print(name_txt1, name_txt2, " ", j)

            # 상품 로드
            if j % 20 == 0:
                while True:
                    xpath_100 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div/app-view-grid/div/ul/li[{j+20}]/app-product/div/div[1]/gc-link/a'
                    xpath_101 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div[2]/app-view-grid/div/ul/li[{j+20}]/app-product/div/div[1]/gc-link/a'
                    if driver.find_elements(By.XPATH, xpath_100) or driver.find_elements(By.XPATH, xpath_101):
                        break
                    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
                    time.sleep(2)

            try:
                xpath_4 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div/app-view-grid/div/ul/li[{j}]/app-product/div/div[1]/gc-link/a'
                link = driver.find_element(By.XPATH, xpath_4)
            except:
                xpath_4 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div[2]/app-view-grid/div/ul/li[{j-12}]/app-product/div/div[1]/gc-link/a'
                link = driver.find_element(By.XPATH, xpath_4)
            url = link.get_attribute('href')
            driver.execute_script("window.open(arguments[0], '_blank');", url)
            time.sleep(2)

            new_handle = [h for h in driver.window_handles if h != original_window][0]
            driver.switch_to.window(new_handle)
            time.sleep(2)

            # 상품명
            name_txt3 = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[1]/h2').get_attribute('textContent')
            print(name_txt3)

            # 상품 가격
            try:
                price_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[2]/div[1]/span[2]')
            except:
                price_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[2]/div[1]/span')
            price = price_loc.text
            price = price.replace("원", "").strip()
            price = price.replace(",", "").strip()
            print(price)

            # 상품 브랜드
            brand_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[4]/gc-link')
            brand = brand_loc.get_attribute('data-tiara-copy')
            print(brand)

            # 상품 이미지
            try:
                img_elem = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[1]/div/cu-carousel/swiper-container/swiper-slide[1]/div/img')
                link_save = img_elem.get_attribute('src')
                print(link_save)
            except NoSuchElementException:
                img_elem = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[1]/div/div/div/img')
                link_save = img_elem.get_attribute('src')
                print(link_save)
                
            # 상품 옵션
            option_list = []
            try:
                option_ul = driver.find_element(By.XPATH, '//*[@id="buyInfo"]/app-layer-product-option/app-bottom-layer/div/div/app-options/div[1]/ul')
                li_elements = option_ul.find_elements(By.TAG_NAME, "li")
                for k in li_elements:
                    option_text = k.find_element(By.TAG_NAME, "label").text
                    option_list.append(option_text)

            except NoSuchElementException:
                print('옵션 없음')
                pass

            print(option_list)

            # 상품 링크
            current_url = driver.current_url
            print("상품 링크:", driver.current_url)

            # 리뷰내용
            try:
                xpath_5 = f'//*[@id="tabList_review"]/span'
                btn_4 = driver.find_element(By.XPATH, xpath_5)
            except:
                xpath_5 = f'//*[@id="tabList_review"]'
                btn_4 = driver.find_element(By.XPATH, xpath_5)
            time.sleep(4)
            btn_4.click()
            time.sleep(2)

            review_list = []
            for l in range(1, 101):
                try:
                    xpath_6 = f'//*[@id="tabPanel_review"]/div/ul/app-view-review-item[{l}]/li'
                    review = driver.find_element(By.XPATH, xpath_6)
                    review_text = review.find_element(By.CSS_SELECTOR, "div:nth-child(1) > div.area_reviewdetail.is_fold > p").text
                    try:
                        tags = review.find_elements(By.CSS_SELECTOR, "div.area_hashtag span.txt_hash")
                        tag_texts = [t.text.strip() for t in tags]

                    except NoSuchElementException:
                        pass

                    if tag_texts:
                        combined = review_text + " " + " ".join(tag_texts)
                    else:
                        combined = review_text
                    review_list.append(combined)

                    # 더보기 클릭
                    if l % 20 == 0:
                        try:
                            btn_5 = driver.find_element(By.CSS_SELECTOR, '#tabPanel_review > div > div.wrap_btn > button')
                            btn_5.click()
                            time.sleep(2)

                        except TimeoutException:
                            pass
                        
                except NoSuchElementException:
                    pass

            print(review_list)

            products_data.append({
                "brand_name": brand,
                "product_name": name_txt3,
                "category_main": name_txt1,
                "category_sub": name_txt2,
                "options": option_list,
                "product_url": current_url,
                "thumbnail_url": link_save,
                "review_content": review_list,
                "price": price
            })

            driver.close()
            driver.switch_to.window(original_window)
            time.sleep(2)
    
        with open(output_path, "w", encoding="utf-8") as f:
            json.dump(products_data, f, ensure_ascii=False, indent=2)

    except NoSuchElementException:
        pass
    

driver.quit()

유아동/반려
고양이 간식/용품
유아동/반려 고양이 간식/용품   1
 고양이 원목 라클라이너 소파 의자 (원목장난감 사냥놀이 스크래쳐 장난감 스크레쳐 호기심유발)  
27900
김멍냥
https://img1.kakaocdn.net/thumb/C320x320@2x.fwebp.q82/?fname=https%3A%2F%2Fst.kakaocdn.net%2Fproduct%2Fgift%2Fproduct%2F20250121160504_3041dd2823574bb3b6c8072224db4cfc.jpg
['리뷰약속 O 케이프 O', '리뷰X 사은품X']
상품 링크: https://gift.kakao.com/product/11061584
['저희아이가 좋아해욯ㅎㅎㅎ 덕분에 냥이들은 못올라갓어요.. #친구에게 받은 #생일 선물', '처음에는 낯설어했는데 아주 좋아하십니다!\n첫째가 안비켜줘서 둘째는 심통부리는중...\n같이 보내주신 케이프도 너무 귀여워요ㅎㅎ #친구에게 받은 #생일 선물', '관심갖아주길 바라며 #친구에게 받은 #생일 선물', '아직은 애기라서 케이프가 크지만 심장너무 아픈거아니예요 ? ㅠㅠㅠㅠ 쇼파는오자마자 조립해서 줬더니\n얼마나 좋아하던지 .. 최고입니다 #친구에게 받은 #반려동물 선물', '너무 귀여워요… ㅠ 계속 앉아있어줘서 행복해요오 #나에게 받은 #반려동물 선물', '배송이 너어어엉어무 늦었어요 ㅠ 이쁘긴 합니다 #친구에게 받은 #반려동물 선물', '귀여운거 짱조아❣️ #친구에게 받은 #생일 선물', '고양이가 아직 경계하지만 좋아하네요🤗 #직장동료에게 받은 #생일 선물', '아이가 너무 좋아해요^_^ #친구에게 받은 #생일 선물', '저희집 야옹이가 너무 좋아합니다 ㅋㅋㅋㅋㅋ\n잘 쓸게요!!! #친구에게 받은 #생일 선물', '5.3kg 꽉 차네요 ㅎㅎ 귀여워요 #친구에게 받은 #생일 선물', '고양이가 좋아해요 근데 원목은 아닌듯 #친구에게 받은 #생일 선물', '후기 쓰는 곳을 못 찾아서 한참 헤맸네요; 처음 왔을 때는 데면데면하더니 이제 제법 

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException
import time
import os
import json
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.common.keys import Keys

# 다운로드 경로
# download_dir = "C:\\KIMUJUNG\\team_project\\final_project\\crawling\\download_json"
download_dir = ".\\download_json"
driver = webdriver.Chrome()

driver.get('https://gift.kakao.com/home?targetType=ALL&rankType=MANY_WISH_RECEIVE&priceRange=20000_29999')
time.sleep(1)

# 디지털/가전
for i in range(1, 12):
    products_data = []

    # 카테고리 클릭
    xpath_1 = f'//*[@id="kakaoWrap"]/sc-gift-header/header/lib-container-pc/div[1]/div/div[1]/button'
    btn_1 = driver.find_element(By.XPATH, xpath_1)
    driver.execute_script("arguments[0].click();", btn_1)
    # btn_1.click()
    time.sleep(2)

    # 디지털/가전
    xpath_2 = f'/html/body/cu-popup-container2/cu-popup-wrapper2/ng-component/app-pc-category-tab/div/div/div[2]/div/div[1]/app-pc-category-l-category/ul/li[11]/a'
    btn_2 = driver.find_element(By.XPATH, xpath_2)
    driver.execute_script("arguments[0].click();", btn_2)
    # btn_2.click()
    time.sleep(2)
    name_txt1 = driver.find_element(By.XPATH, xpath_2).text
    print(name_txt1)

    try:        
        # 세부 카테고리
        xpath_3 = f'//*[@id="tabpan-10"]/ul/li[{i}]/gc-link'
        name_txt2 = driver.find_element(By.XPATH, xpath_3).text
        print(name_txt2)
        
        output_path = os.path.join(download_dir, "products_digital_" + name_txt2.replace('/', '') + ".json")
        btn_3 = driver.find_element(By.XPATH, xpath_3+"/a")
        btn_3.click()
        time.sleep(2)
        
        original_window = driver.current_window_handle

        # 상품 선택
        for j in range(1, 101):
            print(name_txt1, name_txt2, " ", j)

            # 상품 로드
            if j % 20 == 0:
                while True:
                    xpath_100 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div/app-view-grid/div/ul/li[{j+20}]/app-product/div/div[1]/gc-link/a'
                    xpath_101 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div[2]/app-view-grid/div/ul/li[{j+20}]/app-product/div/div[1]/gc-link/a'
                    if driver.find_elements(By.XPATH, xpath_100) or driver.find_elements(By.XPATH, xpath_101):
                        break
                    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
                    time.sleep(2)

            try:
                xpath_4 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div/app-view-grid/div/ul/li[{j}]/app-product/div/div[1]/gc-link/a'
                link = driver.find_element(By.XPATH, xpath_4)
            except:
                xpath_4 = f'//*[@id="mArticle"]/app-pw-home/div/app-category-product-list/cu-infinite-scroll/div/app-category-product-wrapper/div[2]/app-view-grid/div/ul/li[{j-12}]/app-product/div/div[1]/gc-link/a'
                link = driver.find_element(By.XPATH, xpath_4)
            url = link.get_attribute('href')
            driver.execute_script("window.open(arguments[0], '_blank');", url)
            time.sleep(2)

            new_handle = [h for h in driver.window_handles if h != original_window][0]
            driver.switch_to.window(new_handle)
            time.sleep(2)

            # 상품명
            name_txt3 = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[1]/h2').get_attribute('textContent')
            print(name_txt3)

            # 상품 가격
            try:
                price_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[2]/div[1]/span[2]')
            except:
                price_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[2]/div[1]/span')
            price = price_loc.text
            price = price.replace("원", "").strip()
            price = price.replace(",", "").strip()
            print(price)

            # 상품 브랜드
            brand_loc = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[2]/div/div[4]/gc-link')
            brand = brand_loc.get_attribute('data-tiara-copy')
            print(brand)

            # 상품 이미지
            try:
                img_elem = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[1]/div/cu-carousel/swiper-container/swiper-slide[1]/div/img')
                link_save = img_elem.get_attribute('src')
                print(link_save)
            except NoSuchElementException:
                img_elem = driver.find_element(By.XPATH, '//*[@id="mArticle"]/app-home/div/div[1]/app-main/div/div/div[1]/div/div/div/img')
                link_save = img_elem.get_attribute('src')
                print(link_save)
                
            # 상품 옵션
            option_list = []
            try:
                option_ul = driver.find_element(By.XPATH, '//*[@id="buyInfo"]/app-layer-product-option/app-bottom-layer/div/div/app-options/div[1]/ul')
                li_elements = option_ul.find_elements(By.TAG_NAME, "li")
                for k in li_elements:
                    option_text = k.find_element(By.TAG_NAME, "label").text
                    option_list.append(option_text)

            except NoSuchElementException:
                print('옵션 없음')
                pass

            print(option_list)

            # 상품 링크
            current_url = driver.current_url
            print("상품 링크:", driver.current_url)

            # 리뷰내용
            try:
                xpath_5 = f'//*[@id="tabList_review"]/span'
                btn_4 = driver.find_element(By.XPATH, xpath_5)
            except:
                xpath_5 = f'//*[@id="tabList_review"]'
                btn_4 = driver.find_element(By.XPATH, xpath_5)
            time.sleep(7)
            btn_4.click()
            time.sleep(2)

            review_list = []
            for l in range(1, 101):
                try:
                    xpath_6 = f'//*[@id="tabPanel_review"]/div/ul/app-view-review-item[{l}]/li'
                    review = driver.find_element(By.XPATH, xpath_6)
                    review_text = review.find_element(By.CSS_SELECTOR, "div:nth-child(1) > div.area_reviewdetail.is_fold > p").text
                    try:
                        tags = review.find_elements(By.CSS_SELECTOR, "div.area_hashtag span.txt_hash")
                        tag_texts = [t.text.strip() for t in tags]

                    except NoSuchElementException:
                        pass

                    if tag_texts:
                        combined = review_text + " " + " ".join(tag_texts)
                    else:
                        combined = review_text
                    review_list.append(combined)

                    # 더보기 클릭
                    if l % 20 == 0:
                        try:
                            btn_5 = driver.find_element(By.CSS_SELECTOR, '#tabPanel_review > div > div.wrap_btn > button')
                            btn_5.click()
                            time.sleep(2)

                        except TimeoutException:
                            pass
                        
                except NoSuchElementException:
                    pass

            print(review_list)

            products_data.append({
                "brand_name": brand,
                "product_name": name_txt3,
                "category_main": name_txt1,
                "category_sub": name_txt2,
                "options": option_list,
                "product_url": current_url,
                "thumbnail_url": link_save,
                "review_content": review_list,
                "price": price
            })

            driver.close()
            driver.switch_to.window(original_window)
            time.sleep(2)
    
        with open(output_path, "w", encoding="utf-8") as f:
            json.dump(products_data, f, ensure_ascii=False, indent=2)

    except NoSuchElementException:
        pass
    

driver.quit()

디지털/가전
프리미엄 가전
디지털/가전 프리미엄 가전   1
 [빠른배송][NEW 컬러] 리플케이스 - 아이폰 시리즈  
77000
케이스티파이
https://img1.kakaocdn.net/thumb/C320x320@2x.fwebp.q82/?fname=https%3A%2F%2Fst.kakaocdn.net%2Fproduct%2Fgift%2Fproduct%2F20250423173749_5b160ae9507a4dd38928c03998f0177a.png
['아이폰16 시리즈', '아이폰15 시리즈', '아이폰14 시리즈', '아이폰13 시리즈']
상품 링크: https://gift.kakao.com/product/9214998
['케이스티파이 케이스 처음 구매해 봅니다. 다른 케이스와 다를것도 없는데 연예인들 협찬비용 메꾸고 벌어들이느라 케이스 뒤ㅣ지게 비싸다는 것만 알고 있었고, 디자인도 ㅂㄹ인데 무조건 5~7만원인 것만 알고 있어서 첫인상부터 별로라 영원히 살 일 없겠다 싶었어요. 그런데 주위에 너도 나도 다 가지고 있으니, 나도 하나쯤은 가지고 싶고, 빠른배송이란 말에 한 번 구매해 보았습니다. 토요일에 주문하였고 화요일 오전에 배송 출발했다고 카톡이 왔으며, 화요일 저녁에 도착하였다고 카톡이 왔습니다. 케이스티파이 치곤 빠른배송 맞고요, 케이스는 잘 맞습니다. 그립감은 7만7천원이니 당연히 좋아야 겠고요, 이 돈 받고 안 좋으면 사기니까요. 한 번쯤은 구매해도 되지않나 싶습니다. 돈이 넘쳐나거나, 엊그제 상여금을 받았거나, 연예인 협찬비용 지불하고 싶다면 구매해도 나쁘진 않네요. 7만원이 넘는 비용이니 잘 써보겠습니다. #나에게 받은 #평가해보려고 선물', '조명 따라 색이 달라보이는 정말 예쁜 케이스에요! 케이스 치곤 값이 비싸지만 정말 만족 합니다! 대만족!! #나에게 받은 #응원 선물', '일요일에 주문했는데 화요일에 왔고 실물 너무 예븝니다 ㅠㅠ 이 조합으로 꼭 사세요 #나에게 받은 #응원 선물', '배송 무쟈게 빠르고 이뿨요 ❤️\U0001fa77 